In [1]:
# install the neccessary software
%pip install numpy pandas matplotlib seaborn Pillow ipywidgets

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/usr/local/bin/python -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [2]:
#You don't need to change anything in this block, although the modules need to be installed to run this notebook

#We import numpy to handle vectors and some math
import numpy as np

#We import pandas to create a data frame of the experiment data
#Such a table can later be used for plotting our results
import pandas as pd

# Import plotly, which is used for visualization
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'iframe'

In [3]:
#You don't need to change anything in this block

def get_initial_followers_state():
    '''Generates the state of follower particles for t0'''
    followers_positions = 2 * (np.random.rand(num_followers, 2) - 0.5)
    followers_velocities = np.zeros((num_followers, 2))
    return followers_positions, followers_velocities

def get_leader_position(t):
    '''Generates the position of the leader based on input time'''
    step_size = leader_speed
    distance_covered = step_size * t
    
    circle_radius = 1
    circle_circumference = 2 * circle_radius * np.pi
    percent_circle_completed = distance_covered / circle_circumference
    radians = percent_circle_completed * 2 * np.pi
    
    leader_x = np.sin(radians)
    leader_y = np.cos(radians)
    return np.array([leader_x, leader_y])

def magnitude(vector):
    '''Returns the magnitude of a vector'''
    return np.linalg.norm(vector)

def distance_between(position, goal):
    '''Returns the distance between two points'''
    return magnitude(goal - position)

def vector_towards(position, goal):
    '''Returns the vector that points from the position to the goal'''
    return goal - position

def direction_towards(position, goal):
    '''Returns a vector pointing from the position towards the goal with magnitude 1'''
    return (goal - position) / magnitude(goal - position)

def to_dataframe(t, followers_positions, leader_position):
    '''Converts the particle state at one timestep to a dataframe'''
    df = pd.DataFrame()
    df['t'] = np.repeat(t, num_followers + 1)
    df['type'] = np.append(np.repeat('Follower', num_followers), 'Leader')
    df['x'] = np.append(followers_positions[:, 0], leader_position[0])
    df['y'] = np.append(followers_positions[:, 1], leader_position[1])
    df['particle_id'] = list( range( num_followers + 1) )
    return df

In [4]:
#Here we define the possible force functions (attraction / repulsion)
#You can play around with the parameters of the functions or create your own functions
 
def force_random(followers_positions, leader_position, d=0.7, k_followers=0.01, k_leader=0.5): 
    '''Force function with linear attraction and distance proportional, random offset'''
    force = np.zeros((num_followers, 2))
    
    for i in range(num_followers):
        vector_to_leader = vector_towards(followers_positions[i], leader_position)
        force[i] += k_leader * (d - np.random.rand(2)) * vector_to_leader
        
        for j in range(num_followers):
            if i == j:
                continue
            vector_to_follower_j = vector_towards(followers_positions[i], followers_positions[j])
            force[i] += k_followers * (d - np.random.rand(2)) * vector_to_follower_j
    return force

def force_comfortable_distance(followers_positions, leader_position, d=0.5, k_followers=0.1, k_leader=0.5): 
    '''Force function to keep a comfortable distance with linear attraction and repulsion'''
    force = np.zeros((num_followers, 2))
    
    for i in range(num_followers):
        distance_to_leader = distance_between(followers_positions[i], leader_position)
        direction_to_leader = direction_towards(followers_positions[i], leader_position)
        leader_force = k_leader * (distance_to_leader - d) * direction_to_leader
        
        cohesion_force = 0
        for j in range(num_followers):
            if i == j:
                continue
            distance_to_follower_j = distance_between(followers_positions[i], followers_positions[j])
            direction_to_follower_j = direction_towards(followers_positions[i], followers_positions[j])
            cohesion_force += k_followers * (distance_to_follower_j - d) * direction_to_follower_j
            
        force[i] = leader_force + cohesion_force
    return force

In [5]:
# You have two modify this for the task

def force_function3(follower_positions, leader_position, a=0.1, b=0.1, c=0.1):
    return np.zeros_like(follower_positions)


In [6]:
#You don't need to change anything in this block

def update(followers_positions, followers_velocities, leader_position):
    '''Calculates new positions and velocities based on the state given as input'''
    new_velocities = inertia * followers_velocities + force_function(followers_positions, leader_position)
    new_positions = followers_positions + new_velocities
    return new_positions, new_velocities

def run():
    '''Iterates over all time steps, updates the particle states, and writes each state to a dataframe'''
    data = []
    leader_position = get_leader_position(0)
    followers_positions, followers_velocities = get_initial_followers_state()
    data.append(to_dataframe(0, followers_positions, leader_position))
    
    for t in range(1, num_time_steps, 1):
        leader_position = get_leader_position(t)
        followers_positions, followers_velocities = update(followers_positions, followers_velocities, leader_position)
        data.append(to_dataframe(t, followers_positions, leader_position))
        
    return pd.concat(data)

In [7]:
#Here we define some global parameters used in the above functions
#You can change these and observe how the behavior changes

num_followers = 10
leader_speed = 0.1
num_time_steps = 100
inertia = 0.0
force_function = force_random

df = run() #Generate the dataframe for plotting
df.head() # display the first five rows of the dataframe

t      type         x         y  particle_id
0  0  Follower  0.049778  0.648259            0
1  0  Follower  0.396259  0.157471            1
2  0  Follower -0.603413 -0.656886            2
3  0  Follower -0.568764 -0.903861            3
4  0  Follower -0.713796 -0.234486            4

In [9]:
# visualize the data from the dataframe df
# adjust width and hight according to your screen resolution
force_function = force_random

df = run() 
fig = px.scatter(df, x="x", y="y", color='type', symbol="type", animation_frame='t', animation_group='particle_id', width=800, height=800)
fig.update_layout(xaxis_range=(-2.0, 2.0), yaxis_range=(-2.0, 2.0))
fig.show()

In [10]:
# visualize the data from the dataframe df
# adjust width and hight according to your screen resolution
force_function = force_comfortable_distance

df = run()
fig = px.scatter(df, x="x", y="y", color='type', symbol="type", animation_frame='t', animation_group='particle_id', width=800, height=800)
fig.update_layout(xaxis_range=(-2.0, 2.0), yaxis_range=(-2.0, 2.0))
fig.show()

In [11]:
# visualize the data from the dataframe df
# adjust width and hight according to your screen resolution
force_function = force_function3

df = run() 
fig = px.scatter(df, x="x", y="y", color='type', symbol="type", animation_frame='t', animation_group='particle_id', width=800, height=800)
fig.update_layout(xaxis_range=(-2.0, 2.0), yaxis_range=(-2.0, 2.0))
fig.show()